In [1]:
from json import dumps as json_dumps

import marimo as mo
import plotly.express as px
import polars as pl
from bs4 import BeautifulSoup
from bs4.element import Tag
from httpx import get as http_get
from pydantic import BaseModel
from pydantic_ai.agent import Agent
from pydantic_ai.models.openai import OpenAIModel
from pydantic_ai.providers.openai import OpenAIProvider

In [2]:
import plotly.offline
plotly.offline.init_notebook_mode()

In [3]:
_SHAARLI_URL = "https://sebsauvage.net/links/"

class Link(BaseModel):
    id: str
    title: str
    href: str
    description: str
    tags: list[str]

def extract_link(entry_node: Tag) -> Link:
    link_id = entry_node.select_one("a")["id"]

    container_node = entry_node.select_one(".linkcontainer")

    link_node = container_node.select_one(".linktitle a")
    link_href = link_node["href"]
    if link_href == "?" + link_id:
        link_href = ""
    link_title = link_node.text.strip()

    if description_node := container_node.select_one(".linkdescription"):
        link_description = description_node.text.strip()
    else:
        link_description = ""

    link_tags = [
        tag.text.strip() for tag in container_node.select(".linktaglist a")
    ]

    link = Link(
        id=link_id,
        title=link_title,
        href=link_href,
        description=link_description,
        tags=link_tags,
    )

    return link

def extract_links(soup: BeautifulSoup) -> list[Link]:
    return [extract_link(entry_node) for entry_node in soup.select("#linklist li")]

_r = http_get(_SHAARLI_URL)
_r.raise_for_status()

_soup = BeautifulSoup(_r.text, "html5lib")
_links = extract_links(_soup)
links_df = pl.DataFrame(_links)

In [4]:
links_df

shape: (50, 5)
┌────────┬──────────────────────┬──────────────────────┬─────────────────────┬─────────────────────┐
│ id     ┆ title                ┆ href                 ┆ description         ┆ tags                │
│ ---    ┆ ---                  ┆ ---                  ┆ ---                 ┆ ---                 │
│ str    ┆ str                  ┆ str                  ┆ str                 ┆ list[str]           │
╞════════╪══════════════════════╪══════════════════════╪═════════════════════╪═════════════════════╡
│ jYuT9A ┆ </> htmx - high      ┆ https://htmx.org/    ┆ Concevoir des pages ┆ ["web"]             │
│        ┆ power tools fo…      ┆                      ┆ dynamiques…         ┆                     │
│ b186Aw ┆ Dialogue typique     ┆                      ┆ 👨‍🦰 J'ai besoin de   ┆ []                  │
│        ┆ avec une IA          ┆                      ┆ la réponse …        ┆                     │
│ 6gW5Dw ┆ Tiling terminal      ┆ https://www.theregis ┆ Si vous cherchez    ┆ ["Linux",           │
│        ┆ multiplexers f…      ┆ ter.com/20…          ┆ des multiplex…      ┆ "LogicielLibre"]    │
│ 3TTqyQ ┆ Économisez 100 % sur ┆ https://store.steamp ┆ Jeu gratuit sur     ┆ ["gratuit", "jeux"] │
│        ┆ SteamWorl…           ┆ owered.com…          ┆ Steam.              ┆                     │
│ HVNakw ┆ En Alsace, le data   ┆ https://www.rue89str ┆ Sachant que         ┆ []                  │
│        ┆ center de M…         ┆ asbourg.co…          ┆ l'Alsace c'est moi… ┆                     │
│ …      ┆ …                    ┆ …                    ┆ …                   ┆ …                   │
│ lWStRA ┆ Piratage sportif :   ┆ https://next.ink/188 ┆ Ah bah oui après    ┆ ["copyreich"]       │
│        ┆ l’Arcom sur…         ┆ 426/pirata…          ┆ avoir censuré…      ┆                     │
│ 7bTyYA ┆ WhatsApp Introduces  ┆ https://www.nytimes. ┆ La publicité arrive ┆ ["merdification"]   │
│        ┆ Ads in Its…          ┆ com/2025/0…          ┆ dans Whats…         ┆                     │
│ FZk9Tg ┆ Refonder la          ┆ https://friction-mag ┆ Excellent article   ┆ ["LGBT"]            │
│        ┆ solidarité queer :…  ┆ azine.fr/r…          ┆ sur les diss…       ┆                     │
│ _EKv9g ┆ Recrutements         ┆ https://framablog.or ┆ (En complément de   ┆ []                  │
│        ┆ automatisés : déf…   ┆ g/2025/06/…          ┆ https://sebs…       ┆                     │
│ AfBPtA ┆ KAIST Succeeds in    ┆ https://news.kaist.a ┆ Un capteur de CO²   ┆ ["technologie"]     │
│        ┆ Real-Time Ca…        ┆ c.kr/newse…          ┆ qui ne néces…       ┆                     │
└────────┴──────────────────────┴──────────────────────┴─────────────────────┴─────────────────────┘

In [5]:
_OLLAMA_URL = "http://edemaruh:11434/v1"
_LLM_MODEL = "ollama:qwen3:8b"
# LLM_MODEL = "google-gla:gemini-2.5-flash"

_SYSTEM_PROMPT = """\
You are a data classifier. for each content item, determines whether it talks about AI/LLM (True) or not (False). 
"""

_provider_name, _model_name = _LLM_MODEL.split(":", maxsplit=1)
if _provider_name == "ollama":
    _provider = OpenAIProvider(
        base_url=_OLLAMA_URL,
    )
    _model = OpenAIModel(
        model_name=_model_name,
        provider=_provider,
    )
else:
    _model = _LLM_MODEL

_agent = Agent(model=_model, output_type=bool, system_prompt=_SYSTEM_PROMPT)

classified_links_df = links_df.with_columns(
    pl.Series(
        "is_ai",
        [
            (await _agent.run(json_dumps(link))).output
            for link in mo.status.progress_bar(
                links_df.iter_rows(), total=links_df.height
            )
        ],
    )
)

In [6]:
classified_links_df

shape: (50, 6)
┌────────┬────────────────────┬────────────────────┬───────────────────┬───────────────────┬───────┐
│ id     ┆ title              ┆ href               ┆ description       ┆ tags              ┆ is_ai │
│ ---    ┆ ---                ┆ ---                ┆ ---               ┆ ---               ┆ ---   │
│ str    ┆ str                ┆ str                ┆ str               ┆ list[str]         ┆ bool  │
╞════════╪════════════════════╪════════════════════╪═══════════════════╪═══════════════════╪═══════╡
│ jYuT9A ┆ </> htmx - high    ┆ https://htmx.org/  ┆ Concevoir des     ┆ ["web"]           ┆ false │
│        ┆ power tools fo…    ┆                    ┆ pages dynamiques… ┆                   ┆       │
│ b186Aw ┆ Dialogue typique   ┆                    ┆ 👨‍🦰 J'ai besoin de ┆ []                ┆ true  │
│        ┆ avec une IA        ┆                    ┆ la réponse …      ┆                   ┆       │
│ 6gW5Dw ┆ Tiling terminal    ┆ https://www.thereg ┆ Si vous cherchez  ┆ ["Linux",         ┆ false │
│        ┆ multiplexers f…    ┆ ister.com/20…      ┆ des multiplex…    ┆ "LogicielLibre"]  ┆       │
│ 3TTqyQ ┆ Économisez 100 %   ┆ https://store.stea ┆ Jeu gratuit sur   ┆ ["gratuit",       ┆ false │
│        ┆ sur SteamWorl…     ┆ mpowered.com…      ┆ Steam.            ┆ "jeux"]           ┆       │
│ HVNakw ┆ En Alsace, le data ┆ https://www.rue89s ┆ Sachant que       ┆ []                ┆ true  │
│        ┆ center de M…       ┆ trasbourg.co…      ┆ l'Alsace c'est    ┆                   ┆       │
│        ┆                    ┆                    ┆ moi…              ┆                   ┆       │
│ …      ┆ …                  ┆ …                  ┆ …                 ┆ …                 ┆ …     │
│ lWStRA ┆ Piratage sportif : ┆ https://next.ink/1 ┆ Ah bah oui après  ┆ ["copyreich"]     ┆ false │
│        ┆ l’Arcom sur…       ┆ 88426/pirata…      ┆ avoir censuré…    ┆                   ┆       │
│ 7bTyYA ┆ WhatsApp           ┆ https://www.nytime ┆ La publicité      ┆ ["merdification"] ┆ false │
│        ┆ Introduces Ads in  ┆ s.com/2025/0…      ┆ arrive dans       ┆                   ┆       │
│        ┆ Its…               ┆                    ┆ Whats…            ┆                   ┆       │
│ FZk9Tg ┆ Refonder la        ┆ https://friction-m ┆ Excellent article ┆ ["LGBT"]          ┆ false │
│        ┆ solidarité queer   ┆ agazine.fr/r…      ┆ sur les diss…     ┆                   ┆       │
│        ┆ :…                 ┆                    ┆                   ┆                   ┆       │
│ _EKv9g ┆ Recrutements       ┆ https://framablog. ┆ (En complément de ┆ []                ┆ false │
│        ┆ automatisés : déf… ┆ org/2025/06/…      ┆ https://sebs…     ┆                   ┆       │
│ AfBPtA ┆ KAIST Succeeds in  ┆ https://news.kaist ┆ Un capteur de CO² ┆ ["technologie"]   ┆ false │
│        ┆ Real-Time Ca…      ┆ .ac.kr/newse…      ┆ qui ne néces…     ┆                   ┆       │
└────────┴────────────────────┴────────────────────┴───────────────────┴───────────────────┴───────┘

In [7]:
px.pie(
    classified_links_df,
    names="is_ai",
    title="AI/LLM Links Classification",
    color_discrete_sequence=px.colors.qualitative.Pastel,
    hole=0.3,
).show()